# Tensorboard 사용하기

## 학습 로그 디렉토리 생성

In [ ]:
! mkdir -p logs/fit

## 모델 정의 및 학습

In [ ]:
import tensorflow as tf
import datetime

# 학습 데이터 준비
mnist = tf.keras.datasets.mnist
(x_train, y_train),(x_test, y_test) = mnist.load_data()
x_train, x_test = x_train / 255.0, x_test / 255.0

# 모델 정의
model = tf.keras.models.Sequential([
    tf.keras.layers.Flatten(input_shape=(28, 28), name='layers_flatten'),
    tf.keras.layers.Dense(512, activation='relu', name='layers_dense'),
    tf.keras.layers.Dropout(0.2, name='layers_dropout'),
    tf.keras.layers.Dense(10, activation='softmax', name='layers_dense_2')
])

model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])

log_dir = "logs/fit/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")

# 모델 그래프 저장
@tf.function
def model_to_trace(x):
  return model(x)

writer = tf.summary.create_file_writer(log_dir)
with writer.as_default():
    concrete_func = model_to_trace.get_concrete_function(
        tf.TensorSpec([None, 28, 28], tf.float32) # Define input shape and type
    )
    tf.summary.graph(concrete_func.graph)

# 텐서보드 콜백 설정: 정의된 로그 디렉토리를 사용
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir, histogram_freq=1)

# 모델 학습
model.fit(
   x=x_train,
   y=y_train,
   epochs=10,
   validation_data=(x_test, y_test),
   callbacks=[tensorboard_callback],
   verbose=1
)

## Tensorbard 시각화

In [ ]:
from IPython.display import IFrame
TENSORBOARD_URL = "{YOUR TENSORBOARD URL}"
IFrame(TENSORBOARD_URL, '100%', '600px')